### Jupyter-notebook to load the raw experimental data and related acquisition properties

In [ ]:
import mat73
from scipy.interpolate import interp1d
import numpy as np
import matplotlib.pyplot as plt

#### Path and filename in which raw data is located

In [ ]:
path = './Experimental_data/Phantom_I/'
filename = 'acquisition_0.mat'

#### Load data and acquisition parameters 

In [ ]:
# Raw data is saved as matlab v7.3 file:
mat = mat73.loadmat(path + filename)

freq = float(mat['bmode']['p']['tx_freq']) * 1e6         # center frequency [Hz]
pitch = float(mat['bmode']['p']['piezoPitch']) * 1e-3    # distance between elements [m]
c_system = float(mat['bmode']['p']['speedOfSound'])      # assumed SoS by the system [m]
n_elem = int(mat['bmode']['p']['nbPiezos'])              # number of elements in the probe
acq_delay = float(mat['bmode']['p']['peakDelay']) * 1e-6 # acquisition delay [s]

upsample = 4  # upsample to demodulate the signal
fsampling = float(mat['bmode']['p']['bandwidth']) * 1e6 * upsample # sampling frequency [Hz]

# crf-signals [time, elem, angle] (omit the first acquisition angle, often faulty)
data = np.transpose(mat['bmode']['rfr'], (0, 2, 1))[:, :, 1:]

nt = data.shape[0] * upsample # number of time samples 

demodFreq = float(mat['bmode']['p']['demodFreq']) * 1e6  # demodulation frequency [Hz]

time_iq = np.arange(0, data.shape[0]) / (fsampling / upsample)  # vector defining time in recorded signal
time = np.arange(0, nt) / fsampling                             # vector defining time in demodulated signal
carrier = np.exp(2 * np.pi * 1j * demodFreq * time)             # carrier signal for demodulation

## Interpolate signals to upsample
if upsample > 1:

    f = interp1d(time_iq, data, axis=0, kind='cubic', fill_value='extrapolate')
    data = f(time)                

# demodulate recorded signals to recover original crf-signals:
data = np.transpose(np.transpose(data, (2, 1, 0)) * carrier, (2, 1, 0))

# plane wave steering angles used for acquisition
angles_sys = mat['bmode']['p']['steeringAngleList'][1:] * np.pi / 180  # [rad]

# Time delays to the center of the aperture 
tx_delays = mat['bmode']['p']['timeOrigin'][1:] * 1e-6  # [s]

#### Plot an example raw signal

In [ ]:
plt.plot(time, data[:, 0, 0].real)